In [1]:
import json
import torch
import numpy as np
from pathlib import Path
from src import utils
from src.model import RBVPredictor
from PIL import Image
import cv2
import matplotlib.pyplot as plt
import trimesh

In [2]:
data_root = Path("/ssd_scratch/cvit/ishaanshah/tree_dataset/")
model_path = Path("./model/model.ckpt")

In [3]:
model = RBVPredictor.load_from_checkpoint(str(model_path))
model.eval();

In [4]:
def infer(species, idx=0, view=0):
    label = utils.process_label(Image.open(str(data_root / species / str(idx) / str(view) / 'gray_segmentation.png')))
    label = torch.unsqueeze(label, dim=0)
    with open(str(data_root / species / str(idx) / str(view) / 'info.json')) as f:
        gt = json.load(f)['norm_rbv']

    with torch.no_grad():
        x1, _, _, inferred = model(label)
    return torch.tensor(gt), torch.reshape(inferred, (8, 8))

In [5]:
def generate_rbv(rbv, height=1):
    rbv[rbv == 0] = 1e-5
    meshes = []
    segments = rbv.shape[1]*64
    angles = np.linspace(0, 2*np.pi, segments)
    layers = rbv.shape[0]
    sectors = rbv.shape[1]
    for i in range(layers):
        for j in range(sectors):
            n = 64
            angles = np.linspace(2*j*np.pi/sectors, 2*(j+1)*np.pi/sectors, n)
            x = rbv[i,j]*np.cos(angles)
            y = rbv[i,j]*np.sin(angles)
            vertices = np.c_[x, y]
            vertices = np.r_[np.zeros((1,2)), vertices]
            faces = np.c_[np.zeros(n-1), np.arange(n-1)+1, np.arange(n-1)+2]
            mesh = trimesh.creation.extrude_triangulation(vertices, faces, height/layers, process=False)
            mesh.vertices[:,2] += i * height / layers
            meshes.append(mesh)
    
    rbv = trimesh.util.concatenate(meshes)
    return rbv

In [14]:
gt, inferred = infer('maple', 37, 0)
print(torch.abs(gt - inferred).mean())
print(inferred)
print(gt)

tensor(0.0901)
tensor([[0.0839, 0.0865, 0.0832, 0.0820, 0.0876, 0.0911, 0.0918, 0.0880],
        [0.3492, 0.3395, 0.3517, 0.3393, 0.3541, 0.3481, 0.3597, 0.3459],
        [0.5099, 0.5078, 0.5092, 0.5058, 0.5069, 0.5093, 0.5134, 0.5089],
        [0.5306, 0.5344, 0.5318, 0.5332, 0.5304, 0.5375, 0.5350, 0.5347],
        [0.5057, 0.5037, 0.5028, 0.5029, 0.5080, 0.5062, 0.5056, 0.5033],
        [0.4589, 0.4558, 0.4587, 0.4555, 0.4633, 0.4624, 0.4618, 0.4565],
        [0.3853, 0.3833, 0.3900, 0.3898, 0.3962, 0.3924, 0.3938, 0.3860],
        [0.2385, 0.2409, 0.2449, 0.2410, 0.2441, 0.2455, 0.2444, 0.2397]])
tensor([[0.0378, 0.0371, 0.0403, 0.0483, 0.0486, 0.0386, 0.0391, 0.0392],
        [0.1057, 0.0530, 0.5656, 0.5595, 0.5951, 0.5681, 0.1120, 0.0984],
        [0.4866, 0.2081, 0.4096, 0.6016, 0.5592, 0.5400, 0.3512, 0.5087],
        [0.4899, 0.4128, 0.4638, 0.5936, 0.6076, 0.6064, 0.5457, 0.5089],
        [0.4778, 0.4777, 0.3639, 0.4928, 0.5963, 0.6148, 0.5571, 0.4522],
        [0.4214, 0.526

In [30]:
gt_rbv = generate_rbv(gt.numpy())
infer_rbv = generate_rbv(inferred.numpy())
infer_rbv.vertices[:,0] += 1
gt_rbv.vertices[:,0] -= 1
comp = trimesh.util.concatenate([infer_rbv, gt_rbv])
comp.show()

In [17]:
gt, inferred = infer('aspen', 37, 0)
print(torch.abs(gt - inferred).mean())
print(inferred)
print(gt)

tensor(0.0602)
tensor([[0.0347, 0.0317, 0.0332, 0.0323, 0.0310, 0.0305, 0.0309, 0.0347],
        [0.0269, 0.0267, 0.0252, 0.0224, 0.0259, 0.0253, 0.0239, 0.0268],
        [0.1216, 0.1258, 0.1241, 0.1207, 0.1148, 0.1257, 0.1233, 0.1275],
        [0.4799, 0.4814, 0.4854, 0.4699, 0.4791, 0.4789, 0.4886, 0.4817],
        [0.6744, 0.6681, 0.6729, 0.6629, 0.6736, 0.6634, 0.6692, 0.6640],
        [0.6821, 0.6800, 0.6881, 0.6819, 0.6826, 0.6784, 0.6804, 0.6745],
        [0.6099, 0.6119, 0.6160, 0.6154, 0.6126, 0.6121, 0.6123, 0.6080],
        [0.4673, 0.4535, 0.4713, 0.4589, 0.4650, 0.4586, 0.4688, 0.4534]])
tensor([[0.0293, 0.0291, 0.0355, 0.0393, 0.0387, 0.0320, 0.0296, 0.0297],
        [0.0135, 0.0227, 0.0438, 0.0540, 0.0531, 0.0317, 0.0162, 0.0113],
        [0.0394, 0.0000, 0.0935, 0.0524, 0.0796, 0.1489, 0.0817, 0.0475],
        [0.6269, 0.4841, 0.5099, 0.4183, 0.5592, 0.4702, 0.4292, 0.5558],
        [0.8402, 0.6944, 0.6616, 0.6825, 0.7878, 0.7473, 0.7807, 0.8665],
        [0.7144, 0.597

In [18]:
gt_rbv = generate_rbv(gt.numpy())
infer_rbv = generate_rbv(inferred.numpy())
infer_rbv.vertices[:,0] += 1
gt_rbv.vertices[:,0] -= 1
comp = trimesh.util.concatenate([infer_rbv, gt_rbv])
comp.show()

/home2/ishaanshah/anaconda3/envs/botanical_trees/lib/python3.9/site-packages/IPython/core/display.py:414: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [23]:
gt, inferred = infer('oak', 1, 0)
print(torch.abs(gt - inferred).mean())
print(inferred)
print(gt)

tensor(0.1029)
tensor([[0.0624, 0.0646, 0.0605, 0.0568, 0.0604, 0.0674, 0.0691, 0.0692],
        [0.2073, 0.1978, 0.1875, 0.1750, 0.1868, 0.2015, 0.2059, 0.2092],
        [0.4683, 0.4541, 0.4533, 0.4428, 0.4440, 0.4509, 0.4643, 0.4682],
        [0.6027, 0.6030, 0.5910, 0.5981, 0.5890, 0.5977, 0.5997, 0.6131],
        [0.6105, 0.5943, 0.5982, 0.5923, 0.6012, 0.5916, 0.6031, 0.5996],
        [0.5201, 0.5165, 0.5108, 0.5115, 0.5121, 0.5162, 0.5190, 0.5203],
        [0.4017, 0.4003, 0.3961, 0.3971, 0.3948, 0.4012, 0.4021, 0.4052],
        [0.2493, 0.2399, 0.2437, 0.2342, 0.2393, 0.2403, 0.2457, 0.2428]])
tensor([[0.0602, 0.0602, 0.0602, 0.0641, 0.0783, 0.0779, 0.0621, 0.0602],
        [0.0202, 0.1039, 0.1035, 0.0565, 0.0813, 0.3739, 0.2870, 0.1639],
        [0.2988, 0.5608, 0.5404, 0.0000, 0.6153, 0.7086, 0.6055, 0.4335],
        [0.5285, 0.5306, 0.6157, 0.4487, 0.7387, 0.7501, 0.7884, 0.5571],
        [0.5849, 0.5245, 0.5576, 0.5339, 0.5927, 0.6671, 0.7355, 0.6135],
        [0.5596, 0.441

In [24]:
gt_rbv = generate_rbv(gt.numpy())
infer_rbv = generate_rbv(inferred.numpy())
infer_rbv.vertices[:,0] += 1
gt_rbv.vertices[:,0] -= 1
comp = trimesh.util.concatenate([infer_rbv, gt_rbv])
comp.show()